In [1]:
# standard python utilities
import os
from os.path import basename, dirname
import sys
import glob
import pandas as pd
import numpy as np
import calendar
import time

# standard python plotting utilities
import matplotlib as mpl
import matplotlib.pyplot as plt

# standard geospatial python utilities
import pyproj # for converting proj4string
import shapely
import geopandas as gpd
import rasterio

# mapping utilities
import contextily as ctx
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from mpl_toolkits.axes_grid1.anchored_artists import AnchoredSizeBar
import matplotlib.font_manager as fm

# modflow utility
import flopy
import flopy.utils.binaryfile as bf


In [2]:
## Set up directory referencing
# Package data
git_dir = os.path.dirname(os.path.dirname(os.getcwd()))
git_dir = os.getcwd()
while os.path.basename(git_dir) != 'CosumnesRiverRecharge':
    git_dir = os.path.dirname(git_dir)
gwfm_dir = '\\'.join(str.split(git_dir,'\\')[0:3])+ '/Box/research_cosumnes/GWFlowModel'
print(git_dir, gwfm_dir)

C:\Users\ajcalder\Documents\GitHub\CosumnesRiverRecharge C:\Users\ajcalder/Box/research_cosumnes/GWFlowModel


In [140]:
# set box directory for output figures and data
box_dir = gwfm_dir+'/Levee_setback/levee_setback_distance_analysis/'

tprogs_id = '' # original tprogs with conditioning data in output tsim
# tprogs_id = '_no_conditioning'

data_dir = box_dir+ tprogs_id+'/data_output/'
fig_dir = box_dir+tprogs_id+'/figures/'
#
chan_dir = box_dir+'channel_data/'
gis_dir = chan_dir+'GIS/'

check_stream_loc = False
# fig_dir = box_dir+'north_shifted_stream_distance_analysis/figures/'


In [165]:
ext_dir = 'F:/WRDAPP'
c_dir = 'C:/WRDAPP'

if os.path.exists(ext_dir):
    loadpth = ext_dir 
elif os.path.exists(c_dir):
    loadpth = c_dir 

loadpth = loadpth +'/GWFlowModel/Cosumnes/levee_setback/setback_distance_analysis/'
model_ws = loadpth+'Permeameter_for_velocity' + tprogs_id

In [166]:
name = 'MF.nam'
# name = 'MF_child.nam'
m = flopy.modflow.Modflow.load(name, model_ws=model_ws, 
                                exe_name='mf2005', version='mf2005')


In [4]:
# dem data for cropping above land surface
dem_data = np.loadtxt(gwfm_dir+'/DIS_data/dem_52_9_200m_linear.tsv')

In [5]:
grid_p = gpd.read_file(gwfm_dir+'/DIS_data/grid/grid.shp')


C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\geopandas\_vectorized.py:142: DeprecationWarning: An exception was ignored while fetching the attribute `__array_interface__` from an object of type 'Polygon'.  With the exception of `AttributeError` NumPy will always raise this exception in the future.  Raise this deprecation warning to see the original exception. (Warning added NumPy 1.21)
  aout[:] = out
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\geopandas\_vectorized.py:142: DeprecationWarning: An exception was ignored while fetching the attribute `__array_interface__` from an object of type 'Polygon'.  With the exception of `AttributeError` NumPy will always raise this exception in the future.  Raise this deprecation warning to see the original exception. (Warning added NumPy 1.21)
  aout[:] = out
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\geopandas\_vectorized.py:142: DeprecationWarning: An exception was ignored while fetching the attribute `__ar

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\geopandas\_vectorized.py:142: DeprecationWarning: An exception was ignored while fetching the attribute `__array_interface__` from an object of type 'Polygon'.  With the exception of `AttributeError` NumPy will always raise this exception in the future.  Raise this deprecation warning to see the original exception. (Warning added NumPy 1.21)
  aout[:] = out
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\geopandas\_vectorized.py:142: DeprecationWarning: An exception was ignored while fetching the attribute `__array_interface__` from an object of type 'Polygon'.  With the exception of `AttributeError` NumPy will always raise this exception in the future.  Raise this deprecation warning to see the original exception. (Warning added NumPy 1.21)
  aout[:] = out
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\geopandas\_vectorized.py:142: DeprecationWarning: An exception was ignored while fetching the attribute `__ar

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [11]:
import numpy as np

import pyvista as pv
from pyvista import examples

In [12]:
pv.set_jupyter_backend('pythreejs')

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\traittypes\traittypes.py:24: DeprecationWarning: 
            Sentinel is not a public part of the traitlets API.
            It was published by mistake, and may be removed in the future.
            
  """)
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pythreejs\traits.py:276: DeprecationWarning: Keyword `traits` is deprecated in traitlets 5.0, use `per_key_traits` instead
  ), default_value=default_value, **kwargs)
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pythreejs\materials\ShaderMaterial_autogen.py:29: DeprecationWarning: Keyword `trait` is deprecated in traitlets 5.0, use `value_trait` instead
  uniforms = Dict(default_value={}, trait=Uniform(allow_none=True), allow_none=False).tag(sync=True, **uniforms_serialization)


In [138]:
# data = examples.load_channels()
# channels = data.threshold([0.9, 1.1])

In [139]:
# channels.plot(scalars='facies',cmap='viridis')

## TPROGs coarse connectivity

In [141]:
mf_tprogs_dir = gwfm_dir+'/UPW_data/tprogs_final' + tprogs_id+'/'
tprogs_files = glob.glob(mf_tprogs_dir+'*')
# tprogs_files

In [142]:
t=0
tprogs_line = np.loadtxt(tprogs_files[t])
tprogs_arr = np.reshape(tprogs_line, (320, 100,230))

# K, Sy, Ss= int_to_param(tprogs_arr)


When plotting the largest connected mesh it seems to show again all of the coarse facies, which maybe there is an issue with the delination of connectivity. Double check volume of coarse (volume is correct at 25%) and method in case it allows a skip of 1 cell when identifying connectivity.

In [185]:
def mfarr2grid(arr):
    grid = pv.UniformGrid()
    # Set the grid dimensions: shape because we want to inject our values on the
    #   POINT data
    # I have to add 1 to each dimension to have it be built on the cells
    grid.dimensions = [101, 231, 321]
    grid.origin = (645500.0, 4227700.0, -80) # bottom left corner of the dataset
    grid.spacing = (200,200,0.5)
    arr_in = np.moveaxis(arr,0,2).flatten(order='F').astype(int)
    # grid.point_data["facies"] = arr_in
    grid.cell_data["facies"] = arr_in
    return(grid)

grid = mfarr2grid(tprogs_arr)


In [211]:
# and then inspect it!
# mesh.plot(scalars="facies", cmap='viridis', show_edges=False, show_grid=True) #, cpos="xy"
# plotter.set_scale(1, 1, 10)
def grid_plt(grid):
    plotter = pv.Plotter(notebook=False)
    plotter.add_mesh(grid, scalars="facies", cmap='viridis',
    #                  show_edges=True
                    )
    plotter.set_scale(1, 1, 50)
    # plotter.show()
    plotter.show(screenshot=fig_dir+'tprogs.png')
    # plotting looks the same when built on cells instead of points
    
grid_plt(grid)

The mesh is looking pretty close. The side view looks correct for part of it but there is a weird extension that is continuous, maybe an issue with the way I repeated data to make x,y,z

If value is a single value, when invert is True cells are kept when their values are below parameter "value". When invert is False cells are kept when their value is above the threshold "value". Default is False: yielding above the threshold "value".


In [180]:
# filter mesh by facies (1,2 gravel and sand)
coarse = grid.threshold(value = [0.9, 2.1], scalars='facies') #, preference='cell'



C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])


In [17]:
largest = coarse.connectivity(largest=True)


In [145]:
# very long process

bodies = coarse.split_bodies(progress_bar=True)

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

...

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])
C:\Users\ajcalder\Anaconda3\envs\geosp\l

In [37]:
# there are 5480 different blocks each with an unstructured grid which is why it takes so long to load this
# Super titles: Information and Blobkcs
# followed by a table with: Index, Name, Type (e.g., 0, Block-00, UnstructuredGrid, n, Block-n, UnstructuredGrid)
# bodies

In [64]:
# 180,000 looked pretty small, 800,000 too when plotting it
print(200*200*0.5*320,' is the minimum number of cells for vertical connectivity is 320 but')
print(' on average ground surface is at 30 m instead of 80m so really we just need 11/16 of 320')
print( 'so 220 cells minimum cutoff makes ', 200*200*0.5*220)
# using a 220 cell cutoff reduced it to only 45 bodies which is very helpful

# from visual review a sizable chunk (not even fully connected vertically most likely) was 63,640,000.0
# this chunk was the next biggest compared to 0 which shows most of the cells

6400000.0  is the minimum number of cells for vertical connectivity is 320 but
 on average ground surface is at 30 m instead of 80m so really we just need 11/16 of 320
so 220 cells minimum cutoff makes  4400000.0


In [146]:
# # Now remove all bodies with a small volume
for key in bodies.keys():
    b = bodies[key]
    vol = b.volume
    # originally used 4.4E6 next up is 63.6E6
    if vol < 63.E6:
        del bodies[key]
        continue
    # Now lets add a volume array to all blocks
    b.cell_data["TOTAL VOLUME"] = np.full(b.n_cells, vol)

In [147]:
k = bodies.keys()[0]
# print(k)
bodies.keys()
# 0 still looks like it contains every cells
# most don't look like they extend vertically
# while reviewing the connected segments I found that they consider connectivity to be any face, vertex, or corner in touch
# while connec3d offers an option of 6 vs 16
# 2160, 3687 looks a little more substantial

['Block-00']

In [181]:

# # conn.plot()
# plotter = pv.Plotter(notebook=False)
# # plotter.add_mesh(largest, scalars="facies", cmap='viridis')

# # plotter.add_mesh(bodies[k], scalars="facies", cmap='viridis')
# plotter.add_mesh(coarse, scalars="facies", cmap='viridis')

# plotter.set_scale(1, 1, 50)
# plotter.show()

# grid_plt(largest)
# grid_plt(bodies[k])
grid_plt(coarse)

ValueError: Empty meshes cannot be plotted. Input mesh has zero points.

## Permeameter connectivity

In [163]:

all_model_ws = loadpth+'Permeameter_for_velocity' + tprogs_id

In [167]:
for r in np.arange(0,1): #100
#     print('Realization', r, ' time since start ',(time.time()-tic)/60)
    folder = '/realization'+ str(r).zfill(3)+'/'
    run_ws = all_model_ws+folder
        
cbb = flopy.utils.CellBudgetFile(run_ws+'/MF.cbc')
# load velocity in z direction
extcbb = flopy.utils.postprocessing.get_extended_budget(cbb)
(qx, qy, qz) = flopy.utils.postprocessing.get_specific_discharge(vectors = extcbb, model=m)
# convert flow to positive as it is all moving in the downward, -z direction
qz *= -1

In [ ]:
# compare using flow_percentile for individual layer versus entire domain

# tprogs_cleaning.get_tprogs_for_elev(dem_data)
# tprogs_lay = tc.elev_to_tprogs_layers(elev=dem_data,tprogs_top_elev=80, tprogs_bot_elev=-80, num_lays=320)
# elev_to_tprogs_layers?
# rows = np.where(np.ones(tprogs_lay.shape)==1)[0]
# cols = np.where(np.ones(tprogs_lay.shape)==1)[1]
# get high conductivity at ground surface
# qz_plt = np.zeros((100,230))
# qz_plt[rows,cols] = qz[tprogs_lay[rows,cols],rows,cols] 

In [246]:
# first plan, use vertical flow rate to identify high flow recharge cells
q = np.copy(qz)

# because pathways were so vertical when only looking at qz, maybe take average with qx, qy
# take geometric mean
q = (np.abs(qz*qx*qy))**(1/3)

flow_percentile = 95
q_hf = np.zeros(q.shape)
q_hf[q>= np.percentile(q,flow_percentile)] = 1


In [225]:
# temporary fix to highflows on boundaries
# make first, last rows all non-high flow
# idx2cut = [0, 1, -2,-1]
# idx2cut = np.append(np.arange(0,20), np.arange(-30,0))
# qz_hf[:,idx2cut,:] = 0
# same for columns
# qz_hf[:,:,idx2cut] = 0

In [247]:
grid = mfarr2grid(q_hf)


In [248]:

grid_plt(grid)

Looks like limited number of high flow cells on top and bottom, a few vertical sections along the sides when using qz alone.

Use geometry mean of qz, qx, qy seems to show more mixed direction. It almost looks like a random distribution and doesn't look very connected and the bodies that do exist are fairly small.

In [249]:
# filter mesh by flow type (1 = high flow, 0 = low flow) based on qz threshold
coarse = grid.threshold(value = [0.9, 1.1], scalars='facies') #, preference='cell'



C:\Users\ajcalder\Anaconda3\envs\geosp\lib\site-packages\pyvista\core\filters\data_set.py:872: DeprecationWarning: Call to deprecated method ThresholdBetween. (Use 'SetLowerThreshold', 'SetUpperThreshold' and 'SetThresholdFunction' instead.) -- Deprecated since version 9.1.0.
  alg.ThresholdBetween(value[0], value[1])


In [250]:
grid_plt(coarse)

Most of these vertical high flow connected pathways are fairly straight from top to bottom which suggests that water is traveling in a straighter path through the sandy mud/mud to get to the coarse facies rather than a sinuous path only through sand/gravel.

In [251]:
largest = coarse.connectivity(largest=True)


In [252]:
grid_plt(largest)

In [ ]:
# need to find a way to extract the locations of these cells to plot

In [291]:
# largest.get_array('facies')
# cell_data = shows cell data info
# points returns x, y, z for all N points
# cells gives a single value for each cell? Length doesn't match number of cells
largest.cells #['facies']
# 320*100*230
# largest

array([     8, 237836, 237837, ..., 267592, 267593, 267594], dtype=int64)

In [ ]:
# very long process

bodies = coarse.split_bodies(progress_bar=True)